In [ ]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

# The Objective of following notebook is to recommend the movies on the basis of the plot, for that we will be using the wiki plot data and Doc2Vec model  

https://radimrehurek.com/gensim/models/doc2vec.html

In [12]:
!pip install --upgrade gensim
import pandas as pd
import gensim
from gensim.parsing.preprocessing import preprocess_documents
from gensim.models.doc2vec import Doc2Vec, TaggedDocument

### Using the wiki movie plot dataset.

In [13]:
df = pd.read_csv("/kaggle/input/wikipedia-movie-plots/wiki_movie_plots_deduped.csv", sep=",")

#### Dataset overview

In [14]:
df.head()

Release Year                             Title Origin/Ethnicity  \
0          1901            Kansas Saloon Smashers         American   
1          1901     Love by the Light of the Moon         American   
2          1901           The Martyred Presidents         American   
3          1901  Terrible Teddy, the Grizzly King         American   
4          1902            Jack and the Beanstalk         American   

                             Director Cast    Genre  \
0                             Unknown  NaN  unknown   
1                             Unknown  NaN  unknown   
2                             Unknown  NaN  unknown   
3                             Unknown  NaN  unknown   
4  George S. Fleming, Edwin S. Porter  NaN  unknown   

                                           Wiki Page  \
0  https://en.wikipedia.org/wiki/Kansas_Saloon_Sm...   
1  https://en.wikipedia.org/wiki/Love_by_the_Ligh...   
2  https://en.wikipedia.org/wiki/The_Martyred_Pre...   
3  https://en.wikipedia.org/wiki/Terrible_Teddy,_...   
4  https://en.wikipedia.org/wiki/Jack_and_the_Bea...   

                                                Plot  
0  A bartender is working at a saloon, serving dr...  
1  The moon, painted with a smiling face hangs ov...  
2  The film, just over a minute long, is composed...  
3  Lasting just 61 seconds and consisting of two ...  
4  The earliest known adaptation of the classic f...

## Using the movies which were released 2001 onwards as the size of dataset will be much higher will crash the ram 

In [15]:
df = df[df["Release Year"] >= 2001]

In [16]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 12093 entries, 13782 to 34885
Data columns (total 8 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   Release Year      12093 non-null  int64 
 1   Title             12093 non-null  object
 2   Origin/Ethnicity  12093 non-null  object
 3   Director          12093 non-null  object
 4   Cast              11588 non-null  object
 5   Genre             12093 non-null  object
 6   Wiki Page         12093 non-null  object
 7   Plot              12093 non-null  object
dtypes: int64(1), object(7)
memory usage: 850.3+ KB


#### As the goal is to recommend movie using the plot we will be preprocessing the plot and build corpus from it which serve a dataset for the model.

In [17]:
plot_text = df["Plot"].values

#### Preprocess the plot text using the preprocess_documents which covert the text to lowercase, remove punctuation, stop words and stemming the text

In [18]:
processed_text = preprocess_documents(plot_text)
print("the preprocesses document look like :- ")
processed_text

the preprocesses document look like :- 


[['convict',
  'emil',
  'slovak',
  'karel',
  'roden',
  'oleg',
  'razgul',
  'oleg',
  'taktarov',
  'arriv',
  'unit',
  'state',
  'claim',
  'bank',
  'heist',
  'russia',
  'czech',
  'republ',
  'oleg',
  'steal',
  'video',
  'camera',
  'movi',
  'establish',
  'rundown',
  'apart',
  'old',
  'partner',
  'deni',
  'share',
  'emil',
  'fatal',
  'stab',
  'wife',
  'oleg',
  'tape',
  'camera',
  'czech',
  'immigr',
  'daphn',
  'handlova',
  'vera',
  'farmiga',
  'wit',
  'murder',
  'bathroom',
  'escap',
  'kill',
  'hide',
  'crime',
  'emil',
  'burn',
  'apart',
  'jordi',
  'warsaw',
  'edward',
  'burn',
  'arson',
  'investig',
  'assign',
  'case',
  'eddi',
  'flem',
  'robert',
  'niro',
  'flamboy',
  'new',
  'york',
  'citi',
  'detect',
  'call',
  'scene',
  'flem',
  'high',
  'profil',
  'celebr',
  'follow',
  'report',
  'tabloid',
  'stori',
  'host',
  'arrog',
  'robert',
  'hawkin',
  'kelsei',
  'grammer',
  'goe',
  'citizen',
  'cheer',
  'fle

### Tagging the plot with the unique number.

In [19]:
tagged_text = [TaggedDocument(d, [i]) for i, d in enumerate(processed_text)]
tagged_text

[TaggedDocument(words=['convict', 'emil', 'slovak', 'karel', 'roden', 'oleg', 'razgul', 'oleg', 'taktarov', 'arriv', 'unit', 'state', 'claim', 'bank', 'heist', 'russia', 'czech', 'republ', 'oleg', 'steal', 'video', 'camera', 'movi', 'establish', 'rundown', 'apart', 'old', 'partner', 'deni', 'share', 'emil', 'fatal', 'stab', 'wife', 'oleg', 'tape', 'camera', 'czech', 'immigr', 'daphn', 'handlova', 'vera', 'farmiga', 'wit', 'murder', 'bathroom', 'escap', 'kill', 'hide', 'crime', 'emil', 'burn', 'apart', 'jordi', 'warsaw', 'edward', 'burn', 'arson', 'investig', 'assign', 'case', 'eddi', 'flem', 'robert', 'niro', 'flamboy', 'new', 'york', 'citi', 'detect', 'call', 'scene', 'flem', 'high', 'profil', 'celebr', 'follow', 'report', 'tabloid', 'stori', 'host', 'arrog', 'robert', 'hawkin', 'kelsei', 'grammer', 'goe', 'citizen', 'cheer', 'flem', 'warsaw', 'agre', 'work', 'case', 'check', 'crowd', 'warsaw', 'spot', 'daphn', 'try', 'attent', 'disappear', 'emil', 'call', 'escort', 'servic', 'ask', '

####  After the tagging we have to pass the text to the DoctoVec model , here the following standar hyperparameter are used.
* We are using  PV-DBOW (Distributed Bag of Word)architecture of Doc2Vec here we will have 2 vectors :_ the word vector and the doc vector (paragraph vector help in identify the context wrt to paragraph). 
* vector_size = 200 feature vector will have 200 entries.
* window = 2 max dist between current and predicted word.
* hs =1 means that hierarchial softmax will be used for model training.
ref :- https://radimrehurek.com/gensim/models/doc2vec.html

In [20]:
model = Doc2Vec(tagged_text, dm=0, vector_size=200, window=2, min_count=1, epochs=100, hs=1)

### Testing the model by passing the plots of different movies e.g. following is the plot of Harry Potter.

In [21]:
new_doc = "Adaptation of the first of J.K. Rowling's popular children's novels about Harry Potter, a boy who learns on his eleventh birthday that he is the orphaned son of two powerful wizards and possesses unique magical powers of his own. He is summoned from his life as an unwanted child to become a student at Hogwarts, an English boarding school for wizards. There, he meets several friends who become his closest allies and help him discover the truth about his parents' mysterious deaths."

In [22]:
new_doc = gensim.parsing.preprocessing.preprocess_string(new_doc)
test_doc_vector = model.infer_vector(new_doc)
sims = model.docvecs.most_similar(positive = [test_doc_vector])
for s in sims:
    print(f"{(s[1])} | {df['Title'].iloc[s[0]]}")

0.3640515208244324 | Harry Potter and the Philosopher's Stone
0.3418325185775757 | Harry Potter and the Sorcerer's Stone
0.33373749256134033 | Kal Kissne Dekha
0.33196836709976196 | Jumanji: Welcome to the Jungle
0.32614970207214355 | Tomorrow La Scala!
0.32166802883148193 | Yuki Yuna wa Yūsha-bu Shozoku and Yuki Yuna: Washio Sumi Chapter Series
0.31727442145347595 | Congorama
0.3134269714355469 | Flying Swords of Dragon Gate
0.31188681721687317 | The Irregular at Magic High School The Movie: The Girl Who Calls the Stars
0.31182336807250977 | Last Orders


/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:3: DeprecationWarning: Call to deprecated `docvecs` (The `docvecs` property has been renamed `dv`.).
  This is separate from the ipykernel package so we can avoid doing imports until


In [23]:
model.save('Movie_recommend.model')